In [10]:
import math
import pandas as pd
from pathlib import Path
import numpy as np
import os
import matplotlib.pyplot as plt
import h5py


In [11]:
video='Analysis_videos/FPB1/edits_analysis/GH016763edit/GH016763edit.mp4'
# DLCscorer='DLC_resnet50_female_analysisJan6shuffle1_216000'
DLCscorer='DLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000'

dataname = str(Path(video).stem) + DLCscorer + '.h5'
print (dataname)

#loading output of DLC
# Dataframe = pd.read_hdf('/media/paddy/My Passport/Pradeep/Analysis_videos/FPB1/Analysed/13012022/All_trials/GH016763editDLC_resnet50_female_analysisJan6shuffle1_216000_filtered.h5')
Dataframe = pd.read_hdf('Y:/Video Validation/DLC_check/FFBatch/DLC_all_data/bs6197_2downsampledDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5')
Dataframe.head()


GH016763editDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000.h5


scorer      DLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000                 \
individuals                                          goose21                  
bodyparts                                               bill                  
coords                                                     x   y likelihood   
0                                                        NaN NaN        NaN   
1                                                        NaN NaN        NaN   
2                                                        NaN NaN        NaN   
3                                                        NaN NaN        NaN   
4                                                        NaN NaN        NaN   

scorer                                                          ...  \
individuals                                                     ...   
bodyparts   eyeclosed                cheek                head  ...   
coords              x   y likelihood     x   y likelihood    x  ...   
0                 NaN NaN        NaN   NaN NaN        NaN  NaN  ...   
1                 NaN NaN        NaN   NaN NaN        NaN  NaN  ...   
2                 NaN NaN        NaN   NaN NaN        NaN  NaN  ...   
3                 NaN NaN        NaN   NaN NaN        NaN  NaN  ...   
4                 NaN NaN        NaN   NaN NaN        NaN  NaN  ...   

scorer                                                                      \
individuals      single                                                      
bodyparts   frontcamera     rpole                     boat1                  
coords       likelihood         x        y likelihood     x   y likelihood   
0                   1.0  1516.619  197.147        1.0   NaN NaN        NaN   
1                   1.0  1516.643  197.177        1.0   NaN NaN        NaN   
2                   1.0  1516.649  197.194        1.0   NaN NaN        NaN   
3                   1.0  1516.649  197.178        1.0   NaN NaN        NaN   
4                   1.0  1516.643  197.177        1.0   NaN NaN        NaN   

scorer                            
individuals                       
bodyparts   boat2                 
coords          x   y likelihood  
0             NaN NaN        NaN  
1             NaN NaN        NaN  
2             NaN NaN        NaN  
3             NaN NaN        NaN  
4             NaN NaN        NaN  

[5 rows x 474 columns]

Final Function (all geese)

In [12]:
def my_func(ipath,fname,opath):
    Dataframe = pd.read_hdf(ipath+fname)
    Dataframe.head()

    # Relavent info column indices
    g21 = [0,2,5,6,8,11,12,13,14]
    g22 = [27,29,32,33,35,38,39,40,41]
    g23 = [54,56,59,60,62,65,66,67,68]
    g25 = [81,83,86,87,89,92,93,94,95]
    g26 = [108,110,113,114,116,119,120,121,122]
    g27 = [135,137,140,141,143,146,147,148,149]
    g28 = [162,164,167,168,170,173,174,175,176]
    g29 = [189,191,194,195,197,200,201,202,203]
    g30 = [216,218,221,222,224,227,228,229,230]
    g31 = [243,245,248,249,251,254,255,256,257]
    g32 = [270,272,275,276,278,281,282,283,284]
    g33 = [297,299,302,303,305,308,309,310,311]
    g34 = [324,326,329,330,332,335,336,337,338]
    g35 = [351,353,356,357,359,362,363,364,365]
    g36 = [378,380,383,384,386,389,390,391,392]
    g38 = [405,407,410,411,413,416,417,418,419]
    g40 = [432,434,437,438,440,443,444,445,446]

    collist = [g21,g22,g23,g25,g26,g27,g28,g29,g30,g31,g32,g33,g34,g35,g36,g38,g40]
    c = ['goose21','goose22','goose23','goose25','goose26','goose27','goose28','goose29','goose30','goose31','goose32','goose33','goose34','goose35','goose36','goose38','goose40']

    # Looping the output for each individual
    
    for s in range(0,len(collist)):
        print(c[s])
        df = Dataframe[Dataframe.columns[collist[s]]]
        # df_r = df[DLCscorer][c[s]]['collar']['x']
        df_r = df.iloc[:,0:4]
        for k in np.arange(0,len(df_r.iloc[:,0])):
            df.loc[(k),'side_r'] = ""
            df.loc[(k),'side_l'] = ""
            if (df_r.iloc[:,0][k] - df_r.iloc[:,3][k]) < 0:
                df.loc[(k),'side_r'] = "Right"
            elif (df_r.iloc[:,0][k] - df_r.iloc[:,3][k]) > 0:
                df.loc[(k),'side_l'] = "Left"

    ############### OLD IF LOOP ########################        
            # if (df_r.iloc[k])>(df_r.iloc[k-1]):
            #     df.loc[(k),'side_r'] = "Right"
            # elif (df_r.iloc[k])<(df_r.iloc[k-1]):
            #     df.loc[(k),'side_l'] = "Left"

        ##################### Get goose presence based on collar liklihood ##############
        df_pr = df.iloc[:,8]

        for pr in np.arange(0, len(df_pr)):
            if df_pr[pr] >= 0.5:
                df.loc[(pr),'presence'] = "Visible"
            else:
                df.loc[(pr),'presence'] = "Not Visible"

        ####################### Get eye closure vs eye opening based on likelihood #########

        df_eye = df.iloc[:,0:11]
        for eye in np.arange(0, len(df_eye.iloc[:,0])):
            if 'side_r' and 'side_l' in df_eye.columns:   
                if df_eye['side_r'][eye] == "Right":
                    if (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]>= 0.6):
                        df.loc[(eye),'Right_eye'] = "Right Close"
                    elif (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]<= 0.4):
                        df.loc[(eye),'Right_eye'] = "Right Open"
                    elif (df_eye.iloc[:,1][eye] >= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and 0.4<=df_eye.iloc[:,2][eye]<= 0.6):
                        df.loc[(eye),'Right_eye'] = "Not sure"
                    else:   
                        df.loc[(eye),'Right_eye'] = "Right Out of Sight"    
                elif df_eye['side_l'][eye] == "Left":
                    if (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]>= 0.6):
                        df.loc[(eye),'Left_eye'] = "Left Close"
                    elif (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]<= 0.4):
                        df.loc[(eye),'Left_eye'] = "Left Open"
                    elif (df_eye.iloc[:,1][eye] >= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and 0.4<=df_eye.iloc[:,2][eye]<= 0.6):
                        df.loc[(eye),'Left_eye'] = "Not sure"
                    else:   
                        df.loc[(eye),'Left_eye'] = "Left Out of Sight"
                else:   
                    df.loc[(eye),'Right_eye'] = ""
                    df.loc[(eye),'Left_eye'] = ""    
            elif 'side_r' in df_eye.columns:
                if df_eye['side_r'][eye] == "Right":
                    if (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]>= 0.6):
                        df.loc[(eye),'Right_eye'] = "Right Close"
                    elif (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]<= 0.4):
                        df.loc[(eye),'Right_eye'] = "Right Open"
                    elif (df_eye.iloc[:,1][eye] >= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and 0.4<=df_eye.iloc[:,2][eye]<= 0.6):
                        df.loc[(eye),'Right_eye'] = "Not sure"
                    else:   
                        df.loc[(eye),'Right_eye'] = "Right Out of Sight"
                else:   
                    df.loc[(eye),'Right_eye'] = "Right Out of Sight"        
            elif 'side_l' in df_eye.columns:
                if df_eye['side_l'][eye] == "Left":
                    if (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]>= 0.6):
                        df.loc[(eye),'Left_eye'] = "Left Close"
                    elif (df_eye.iloc[:,1][eye]>= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and df_eye.iloc[:,2][eye]<= 0.4):
                        df.loc[(eye),'Left_eye'] = "Left Open"
                    elif (df_eye.iloc[:,1][eye] >= 0.9 and df_eye.iloc[:,4][eye] >= 0.9 and 0.4<=df_eye.iloc[:,2][eye]<= 0.6):
                        df.loc[(eye),'Left_eye'] = "Not sure"
                    else:   
                        df.loc[(eye),'Left_eye'] = "Left Out of Sight"
                else:   
                        df.loc[(eye),'Left_eye'] = "Left Out of Sight"
            else:
                df.loc[(eye),'Error'] = "Error"                                  

        
        df.to_csv(opath+fname[0:22]+'_{}.csv'.format(c[s]))

In [13]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6165_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose34


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose35


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose36
bs6165_8downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [14]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6167_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose38


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose40


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

In [15]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6169_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose34


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose35


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose36
bs6169_8downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [16]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6170_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose26


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose27


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose28
bs6170_9downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [17]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6171_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose26


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose27


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose28
bs6171_5downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [18]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6172_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose38


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose40


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

In [37]:
import os
import fnmatch
arr = ['bs6173_8downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5']

ipath = 'H:\\20220725_chunks\\bs6173_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
# for file in os.listdir(ipath):
#     if file.endswith("filtered.h5"):
#         arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose38


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose40


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

In [20]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6174_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose35


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose36


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose38
bs6174_7downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [29]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6175_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose27


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose28


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose29
bs6175_37downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [22]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6190_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose26


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose27


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose28
bs6190_9downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [28]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6191_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose25


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose26
bs6191_8downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [24]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6192_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose38


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose40


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

In [25]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6193_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

goose25


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose26


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose27
bs6193_9downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el_filtered.h5


In [30]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6196_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


...

C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose38


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose40


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

In [36]:
import os
import fnmatch
arr = []

ipath = 'H:\\20220725_chunks\\bs6197_down\\'
opath = 'C:\\Users\\labgrprattenborg\\Desktop\\Pradeep\\20220725_DLC_extract\\'
for file in os.listdir(ipath):
    if file.endswith("filtered.h5"):
        arr.append(file)          

# print(ori, "has the keyword")

for f in arr: 
    try:          
        my_func(ipath,f,opath)
    except IndexError:
        print(f)

goose21


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose22


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose23


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose25


C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_r'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(k),'side_l'] = ""
C:\Users\labgrprattenborg\AppData\Local\Temp\ipykernel_37660\132805203.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = 

goose26
bs6197_41downsampledcroppedDLC_dlcrnetms5_gooseproj2022Sep15shuffle1_200000_el.h5


END OF EXTRACTION FUNCTION